# Exercise 8: Sound transformations

In this exercise you will use the HPS model to creatively transform sounds. There are two parts in this exercise. In the first one you should perform a natural sounding transformation on the speech sound that you used in the previous exercise (E7). In the second part you should select a sound of your choice and do a "creative" transformation. You will have to write a short description of the sound and of the transformation you did, giving the link to the original sound and uploading several transformed sounds.

For this exercise, you can use the `transformations_GUI.py` (in `software/transformations_interface/`) to try things, once decided you can fill up the code in this file. You can also do everything from here and add any new code you wish.

In order to perform a good/interesting transformation you should make sure that you have performed an analysis that is adequate for the type of transformation you want to do. Not every HPS analysis representation will work for every type of sound transformation. There will be things in the analysis that when modified will result in undesired artifacts. In general, for any transformation, it is best to have the harmonic values as smooth and continuous as possible and an stochastic representation as smooth and with as few values as possible. It might be much better to start with an analysis representation that does not result in the best reconstruction in exchange of having smoother and more compact data.

To help you with the exercise, we give a brief description of the transformation parameters used by the HPS transformation function:

1. `freqScaling`: frequency scaling factors to be applied to the harmonics of the sound, in time-value pairs (where value of 1 is no scaling). The time values can be normalized, from 0 to 1, or can correspond to the times in seconds of the input sound. The scaling factor is a multiplicative factor, thus a value of 1 is no change. Example: to transpose an octave the sound you can specify `[0, 2, 1, 2]`.
2. `freqStretching`: frequency stretching factors to be applied to the harmonics of the sound, in time-value pairs (value of 1 is no stretching). The time values can be normalized, from 0 to 1, or can correspond to the times in seconds of the input sound. The stretching factor is a multiplicative factor whose effect depend on the harmonic number, higher harmonics being more affected that lower ones, thus resulting in an inharmonic effect. A value of 1 results in no transformation. Example: an array like `[0, 1.2, 1, 1.2]` will result in a perceptually large inharmonic effect.
3. `timbrePreservation`: 1 preserves the original timbre, 0 does not. It can only have a value of 0 or of 1. By setting the value to 1 the spectral shape of the original sound is preserved even when the frequencies of the sound are modified. In the case of speech it would correspond to the idea of preserving the identity of the speaker after the transformation.
4. `timeScaling`: time scaling factors to be applied to the whole sound, in time-value pairs (value of 1 is no scaling). The time values can be normalized, from 0 to 1, or can correspond to the times in seconds of the input sound. The time scaling factor is a multiplicative factor, thus 1 is no change. Example: to stretch the original sound to twice the original duration, we can specify `[0, 0, 1, 2]`.

All the transformation values can have as many points as desired, but they have to be in the form of an array with time-value pairs, so of even size. For example a good array for a frequency stretching of a sound that has a duration of 3.146 seconds could be: `[0, 1.2, 2.01, 1.2, 2.679, 0.7, 3.146, 0.7]`.

## Part 1. Perform natural sounding transformations of a speech sound

Use the HPS model with the sound `speech-female.wav`, available in the sounds directory, to first analyze and then obtain a natural sounding transformation of the sound. The synthesized sound should sound as different as possible to the original sound while sounding natural. By natural we mean that it should sound like speech, that it could have been possible to be produced by a human, and by listening we should consider it as a speech sound, even though we might not be able to understand it. You should first make sure that you start from a good analysis, then you can do time and/or frequency scaling transformations. The transformation should be done with a single pass, no mixing of sounds coming from different transformations. Since you used the same sound in A7, use that experience to get a good analysis, but consider that the analysis, given that we now want to use it for applying a very strong transformation, might be done differently than what you did in A7.

Write a short paragraph for every transformation, explaining what you wanted to obtain and explaining the transformations you did, giving both the analysis and transformation parameter values (sufficiently detailed for the evaluator to be able to reproduce the analysis and transformation).

In [1]:
import numpy as np
import matplotlib.pyplot as plt
from scipy.signal import get_window
import sys, os
sys.path.append('../software/models/')
sys.path.append('../software/transformations/')
import utilFunctions as UF
import stft as STFT
import hpsModel as HPS
import hpsTransformations as HPST
import harmonicTransformations as HT
import IPython.display as ipd

In [2]:
# 1.1 perform an analysis/synthesis using the HPS model
'''
input_file = '../sounds/speech-female.wav'

### set the parameters
window ='XXX'
M = XXX
N = XXX
t = XXX
minSineDur = XXX
nH = XXX 
minf0 = XXX
maxf0 = XXX
f0et = XXX
harmDevSlope = XXX
stocf = XXX
'''
input_file = '../sounds/speech-female.wav'

### fill the parameters
window ='blackman'
M = 2647
N = 4096
t = -100
minSineDur = 0.05
nH = 60 
minf0 = 100
maxf0 = 250
f0et = 8
harmDevSlope = 0.001
stocf = 0.2


# no need to modify anything after this
Ns = 512
H = 128

(fs, x) = UF.wavread(input_file)
w = get_window(window, M, fftbins=True)
hfreq, hmag, hphase, stocEnv = HPS.hpsModelAnal(x, fs, w, N, H, t, nH, minf0, maxf0, f0et, harmDevSlope, minSineDur, Ns, stocf)
y, yh, yst = HPS.hpsModelSynth(hfreq, hmag, hphase, stocEnv, Ns, H, fs)

print('Original signal')
ipd.display(ipd.Audio(data=x, rate=fs))
print('HPS synthetised signal')
ipd.display(ipd.Audio(data=y, rate=fs))
print('HPS harmonic signal')
ipd.display(ipd.Audio(data=yh, rate=fs))
print('HPS stochastic signal')
ipd.display(ipd.Audio(data=yst, rate=fs))

Original signal


HPS synthetised signal


HPS harmonic signal


HPS stochastic signal


In [3]:
# 1.2 Perform a transformation from the previous analysis

### define the transformations
freqScaling = np.array([0,0.9, .2,.8, .3,.7, .4,.6, .5,.5, .6,.4, .7,.5, .8,.6, .9,.7, 1,1, 1.3, 2])
#freqStretching = np.array([0, 1.05, 1, 1.5])
freqStretching = np.array([0, 1, 2, 1.1, 2.5, .999, 3, 1.1])

timbrePreservation = 1
timeScaling = np.array([0,0, .7,.9, 1,1.9])


# no need to modify the following code 
Ns = 512
H = 128

# frequency scaling of the harmonics 
hfreqt, hmagt = HT.harmonicFreqScaling(hfreq, hmag, freqScaling, freqStretching, timbrePreservation, fs)

# time scaling the sound
yhfreq, yhmag, ystocEnv = HPST.hpsTimeScale(hfreqt, hmagt, stocEnv, timeScaling)

# synthesis from the trasformed hps representation 
y, yh, yst = HPS.hpsModelSynth(yhfreq, yhmag, np.array([]), ystocEnv, Ns, H, fs)

ipd.display(ipd.Audio(data=y, rate=fs))

### Explain Part 1

As a point of departure, I got the same parameters from the last assignment (A7) and started from here.

In this part, what I did on that female speech sound in order to keep sounding still "natural" have been the follow:
Starting from the frequency scaling, what I tried to achieve here is an down and up "glissando" on the entire duration, moreover I did a tiny frequency stretching adjustement to not apply so much inharmonicity, and last but not least, I tried to change the tempo of the speech by speeding down, especially on the last  words: "es cega", trying to achieve a pronounced stop and finish the sentence slow and somehow whispering.


## Part 2. Perform creative transformations with a sound of your choice

Pick any natural and harmonic sound from Freesound and use the HPS model to do the most creative and interesting transformation you can come up with. Sounding as different as possible from the original sound.

It is essential that you start with a natural harmonic sound. Examples include (but not limited to) any acoustic harmonic instrument, speech, harmonic sound from nature, etc. As long as they have a harmonic structure, you can use it. You can even reuse the sound you used in A7-Part2 or upload your own sound to freesound and then use it.

The sound from Freesound to use could be in any format, but to use the sms-tools software you will have to first convert it to be a monophonic file (one channel), sampling rate of 44100, and 16bits samples.

You can do any interesting transformation with a single pass. It is not allowed to mix sounds obtained from different transformations. The transformed sound need not sound natural. So, time to show some creativity!

Write a short paragraph for every transformation, explaining what you wanted to obtain and explaining the transformations you did, giving both the analysis and transformation parameter values (sufficiently detailed for the evaluator to be able to reproduce the analysis and transformation).

In [4]:
# 1.1 perform an analysis/synthesis using the HPS model

### set the parameters
input_file = '../sounds/saxophone.wav'
window ='blackman'
M = 1001
N = 4096
t = -100
minSineDur = 0.05
nH = 75 
minf0 = 200
maxf0 = 500
f0et = 7
harmDevSlope = 0.01
stocf = 0.2

# no need to modify anything after this
Ns = 512
H = 128

(fs, x) = UF.wavread(input_file)
w = get_window(window, M, fftbins=True)
hfreq, hmag, hphase, stocEnv = HPS.hpsModelAnal(x, fs, w, N, H, t, nH, minf0, maxf0, f0et, harmDevSlope, minSineDur, Ns, stocf)
y, yh, yst = HPS.hpsModelSynth(hfreq, hmag, hphase, stocEnv, Ns, H, fs)

ipd.display(ipd.Audio(data=x, rate=fs))
ipd.display(ipd.Audio(data=y, rate=fs))

../software/models/utilFunctions.py:52: WavFileWarning: Chunk (non-data) not understood, skipping it.
  fs, x = read(filename)


In [17]:
# 1.2 Perform a transformation from the previous analysis

### define the transformations
freqScaling = np.array([0,1, 
                        0.12,1,
                        0.125,1.3, 
                        0.245,1.3,
                        0.3,1.5, 
                        0.495,1.5,
                        0.5,1.122, 
                        0.62,1.122,
                        0.625,1.335, 
                        0.745,1.335,
                        0.75,0.6, 
                        0.8,0.5 ,
                        0.9,.4, 
                        1.0,0.3])

freqStretching = np.array([0,.9, 1,.6, 2.5,.9, 3,.6, 4,.9])

timbrePreservation = .6
timeScaling = np.array([0,0, .9,1.2, 1,1])


# no need to modify anything after this
Ns = 512
H = 128

# frequency scaling of the harmonics 
hfreqt, hmagt = HT.harmonicFreqScaling(hfreq, hmag, freqScaling, freqStretching, timbrePreservation, fs)

# frequency scaling of the harmonics (NEW ONE)
hfreqt, hmagt = HT.harmonicFreqScaling(hfreqt, hmag, np.array([0,1,.8,1]), np.array([0,1.5,1,1]), timbrePreservation, fs)

# time scaling the sound
yhfreq, yhmag, ystocEnv = HPST.hpsTimeScale(hfreqt, hmagt, stocEnv, timeScaling)

# synthesis from the trasformed hps representation 
y, yh, yst = HPS.hpsModelSynth(yhfreq, yhmag, np.array([]), ystocEnv, Ns, H, fs)

ipd.display(ipd.Audio(data=y, rate=fs))

### Explain Part 2

First off, the analysis of the sound by looking at its stft:

I chose the blackman one, because of its low side lobes.
M shoud be bigger or equal than 901 (finally I used 1001), because of taking into account the possible f0 (Dmaj == 294 Hz) we can compute it that way:
6 * 44100/ 294 = 901.
Regarding N, I chose 4096 in order to have zero padding and have good freq resolution and hence, a smoother spectrum. 
Based on Fs/2 / f0 = 22050/294 = 75, but we can get a good pitch sensation by putting the number of harmonics to 60 
The frequency range between the minimum and maximum frequencies is around 300 (flow=200 and fhigh=500) after checking the spectrum and analising the fundamental.
Last params I have used: f0et = 7
harmDevSlope = 0.01
stocf = 0.25

For the given trasformation, and on the process of creativity, I tried a simple timeScaling, as I did not want so much  scaling. At the very end of the signal (0,9) there is a tiny speed down and then back to normal. Then, on the frequency domain, on th one hand I was looking for some sort of triangle envelope, so in that way what I intended to do is going up in slowly and fall down more quickly. On the other hand, when it comes to frequency stretching, aka inhrmonicity, what I tried to do is simultate a saw tooth in order to have inharmonicity evenly distributed.

I created a new harmonicFreqScaling process, so from the output of the first harmonicFreqScaling function, I have used another one, with less parameters on the frequency scaling and freq Stretching. Just for fun. I think playing in that way would be quite interesting also.


